# Notebook Three

In this notebook, we match the TSC (that has already been matched with the YPC) with the index cards.
<br>
We also create subtables for each TSC star with relevant YPC and ALL observation details.

In [1]:
%pylab inline
from astropy.table import Table, hstack,vstack, Column, QTable
from astropy.io import fits
import astropy.units as u
from astropy.coordinates import SkyCoord
from astropy.coordinates import FK5
from astropy.time import Time
from astropy.coordinates import Angle
from astropy.io import ascii
import numpy.ma as ma

Populating the interactive namespace from numpy and matplotlib


### Read in data

In [2]:
#read in the table that was created at the end of notebook two
tsc = Table.read('/Users/JanviMadhani/thaw_star_catalog/finaltable.csv')  # change the filepath to the location on your computer

In [3]:
### Add in empty columns to hold 1950 coordinates that we will precess to later, and a column for publication date
RA1950 = Column(np.arange(len(tsc)), name='Precessed RA1950')
tsc.add_column(RA1950, index=10)
tsc['Precessed RA1950'] = tsc['Precessed RA1950'].astype(str)

Dec1950 = Column(np.arange(len(tsc)), name='Precessed Dec1950')
tsc.add_column(Dec1950, index=11)
tsc['Precessed Dec1950'] = tsc['Precessed Dec1950'].astype(str)

pubdate = Column(np.arange(len(tsc)), name='AO Publication Year')
tsc.add_column(pubdate, index=24)
tsc['AO Publication Year'] = tsc['AO Publication Year'].astype(object)


In [4]:
tsc.colnames

['Thaw Number',
 'YPC Number',
 'YPC Component',
 'Thaw Name',
 'YPC Name',
 'BD Number',
 'Thaw RA1900',
 'Thaw Dec1900',
 'Thaw RA1950',
 'Thaw Dec1950',
 'Precessed RA1950',
 'Precessed Dec1950',
 'YPC RA1900',
 'YPC Dec1900',
 'RA2000',
 'Dec2000',
 'Thaw Mag',
 'YPC (B-V)',
 'YPC V',
 'Thaw Spectrum',
 'YPC Spectrum',
 'Thaw Rel. Parallax',
 'Thaw Rel. Parallax Error',
 'Delta Pi',
 'AO Publication Year',
 'Thaw Abs. Parallax',
 'Yale Abs. Parallax',
 'Yale Abs. Parallax Error',
 'Yale Tot. PM',
 'Yale PM Position Angle',
 'No. of Thaw Observations',
 'Thaw Footnotes']

In [5]:
#this is named incorrectly, rename it
#tsc['Dec-00'].name = 'Dec2000'

## Precess to 1950 Coordinates using YPC 1900 Coordinates

In [6]:
def convert_to_J1950(ra,dec,start_equinox='J1900'):
    """
    Precess to 1950 coordinates
    Input parameters: RA hour, min, seconds,
                  Dec deg, min, seconds
                  Starting equinox: default = 1900
    Returns: RA in format: 00h00m00.00s
             Dec in format: 00d00m00.00s
    """
        
    if ra:
        
        fk0c = SkyCoord(ra, dec, unit=(u.hourangle, u.deg), frame=FK5(equinox=Time(start_equinox)))
        fk0_1950 = FK5(equinox='J1950')
        c = fk0c.transform_to(fk0_1950,type)
        string = c.to_string('hmsdms',sep=(' ',' '))
        ra1950 = string[:12]
        dec1950 = string[14:]
        
        
    else:
        ra1950,dec1950 = 0,0
        c = 0 

    
    return(ra1950,dec1950)

In [7]:
ra = '00 13 0.00'
dec = '+36 14 0.00'
convert_to_J1950(ra,dec)

('00 15 36.740', '+36 30 40.4597')

In [8]:
#Fill out values for the 1950 coordinates that we made columns for in the tsc table, 
#and if there is a reported value, fill that in the precessed column as well 

for i in range(len(tsc)):
    ra = tsc['YPC RA1900'][i]
    dec = tsc['YPC Dec1900'][i]
    ra1950,dec1950 = convert_to_J1950(ra,dec)
    tsc['Precessed RA1950'][i] = ra1950
    tsc['Precessed Dec1950'][i] = dec1950
    
    if tsc['Thaw RA1950'][i]:
        tsc['Precessed RA1950'][i] = tsc[i]['Thaw RA1950']
        tsc['Precessed Dec1950'][i] = tsc[i]['Thaw Dec1950']

In [9]:
#Fill out values for publication dates

for i in range(len(tsc)):
    if not ma.is_masked(tsc['Thaw Number'][i]):
        thaw_num = int(tsc['Thaw Number'][i][:4])
        if thaw_num <= 50:
            year = 1917
        elif 50 < thaw_num <= 81:
            year = 1916
        elif 81 < thaw_num <= 160:
            year = 1917
        elif 160 < thaw_num <= 213:
            year = 1918
        elif 213 < thaw_num <= 236:
            year = 1919
        elif 236 < thaw_num <= 285:
            year = 1917
        elif 285 < thaw_num <= 319:
            year = 1919
        elif 319 < thaw_num <= 469:
            year = 1920
        elif 469 < thaw_num <= 592:
            year = 1921
        elif 592 < thaw_num <= 642:
            year = 1923
        elif thaw_num == 643:
            year = 9999
        elif 643 < thaw_num <= 645:
            year = 1925
        elif 645 < thaw_num <= 669:
            year = 1926
        elif 669 < thaw_num <= 719:
            year = 1924
        elif 719 < thaw_num <= 779:
            year = 1927
        elif 779 < thaw_num <= 805:
            year = 1929
        elif 805 < thaw_num <= 855:
            year = 1930
        elif 855 < thaw_num <= 963:
            year = 1931
        elif 963 < thaw_num <= 1063:
            year = 1932
        elif 1063 < thaw_num <= 1086:
            year = 1933
        elif 1086 < thaw_num <= 1263:
            year = 1934
        elif 1263 < thaw_num <= 1363:
            year = 1935
        elif 1363 < thaw_num <= 1413:
            year = 1936
        elif 1413 < thaw_num <= 1450:
            year = 1937
        elif 1450 < thaw_num <= 1510:
            year = 1939
        elif 1510 < thaw_num <= 1560:
            year = 1938
        elif 1560 < thaw_num <= 1600:
            year = 1941
        elif 1600 < thaw_num <= 1650:
            year = 1948
        elif 1650 < thaw_num <= 1773:
            year = 1951
        elif 1773 < thaw_num <= 1863:
            year = 1956
        elif 1863 < thaw_num <= 1918:
            year = 1959
        elif 1918 < thaw_num <= 1978:
            year = 1962
        elif 1978 < thaw_num <= 2045:
            year = 1966
        elif 2045 < thaw_num <= 2070:
            year = 1971
            
            
            
    else:
        year = ''
    
    tsc['AO Publication Year'][i] = str(year)

In [10]:
#Reformat these columns as strings because they prove problematic later if they are not saved as strings


tsc['Yale Abs. Parallax'] = tsc['Yale Abs. Parallax'].astype(str)
tsc['Yale Abs. Parallax Error'] = tsc['Yale Abs. Parallax Error'].astype(str)
tsc['YPC Spectrum'] = tsc['YPC Spectrum'].astype(str)
tsc['YPC V'] = tsc['YPC V'].astype(str)
tsc['YPC (B-V)'] = tsc['YPC (B-V)'].astype(str)

for i in range(len(tsc)):
    s1 = tsc['YPC Spectrum'][i]
    s1 = (str(s1.astype(str)))
    tsc['YPC Spectrum'][i] = s1

    s2 = tsc['YPC V'][i]
    s2 = (str(s2.astype(str)))    
    tsc['YPC V'][i] = s2 
    
    s3 = tsc['YPC (B-V)'][i]
    s3 = (str(s3.astype(str)))  
    tsc['YPC (B-V)'][i] = s3

    

In [11]:
tsc.colnames

['Thaw Number',
 'YPC Number',
 'YPC Component',
 'Thaw Name',
 'YPC Name',
 'BD Number',
 'Thaw RA1900',
 'Thaw Dec1900',
 'Thaw RA1950',
 'Thaw Dec1950',
 'Precessed RA1950',
 'Precessed Dec1950',
 'YPC RA1900',
 'YPC Dec1900',
 'RA2000',
 'Dec2000',
 'Thaw Mag',
 'YPC (B-V)',
 'YPC V',
 'Thaw Spectrum',
 'YPC Spectrum',
 'Thaw Rel. Parallax',
 'Thaw Rel. Parallax Error',
 'Delta Pi',
 'AO Publication Year',
 'Thaw Abs. Parallax',
 'Yale Abs. Parallax',
 'Yale Abs. Parallax Error',
 'Yale Tot. PM',
 'Yale PM Position Angle',
 'No. of Thaw Observations',
 'Thaw Footnotes']

In [12]:
#set the data type for these columns

tsc['YPC Number'] = tsc['YPC Number'].astype(object)
tsc['YPC Name'] = tsc['YPC Name'].astype(str)
tsc['YPC RA1900'] = tsc['YPC RA1900'].astype(str)
tsc['YPC Dec1900'] = tsc['YPC Dec1900'].astype(str)
tsc['YPC (B-V)'] = tsc['YPC (B-V)'].astype(str)
tsc['YPC V'] = tsc['YPC V'].astype(str)
tsc['YPC Spectrum'] = tsc['YPC Spectrum'].astype(str)
tsc['Yale Abs. Parallax'] = tsc['Yale Abs. Parallax'].astype(str)
tsc['Yale Abs. Parallax Error'] = tsc['Yale Abs. Parallax Error'].astype(str)
tsc['Yale Tot. PM'] = tsc['Yale Tot. PM'].astype(str)



#tsc.show_in_notebook()

In [14]:
tsc.show_in_notebook()

## Format Francis' Table

In [15]:
with open('/Users/JanviMadhani/thaw_star_catalog/TSC.txt', 'r+') as data:
    lines = data.readlines()

In [16]:
#read out each entry and append the indices that indicate the start of a new entry to a separate list 

check1 = '999999 x 99999999 9 9\n'
check2 = '999999 x 99999999 9\n'

match_entries = []
match_indices = []
match_entries.append(lines[1])

for i in range(len(lines)):
    if lines[i] == check2:
        match_entries.append(lines[i+1]) 
        match_indices.append(i)
        
    elif lines[i] == check2:
        match_entries.append(lines[i+1])
        match_indices.append(i)
        

In [17]:
#skips the first index, so add it in manually
match_indices.insert(0,0)

In [18]:
print(len(match_indices))
print(len(match_entries))
print(lines[28])
print(lines[851:900])
test_split = match_entries[1].split()
print(test_split)
print(len(test_split))

2577
2577
33203 k 19240808

['999999 x 99999999 9\n', 'beta_1027 7.5 00 13 21.4 _ _ _\n', '52909 k 19351013\n', '69539 k 19451016\n', '78106 g 19501017\n', '83181 g 19531009\n', '999999 x 99999999 9 \n', 'LFT_26 14.5 00 13 37 +19 35.6 _ 1950\n', '93941 f 19610831\n', '93970 k 19610901\n', '94364 k 19611110 (5)\n', '101156 k 19670807\n', '999999 x 99999999 9\n', 'Sigma_16 7.7 00 14 01 +54 22 58 1950\n', '10044 u 19170804\n', '10102 k 19170816\n', '10126 f 19170817\n', '11512 k 19171214\n', '11538 k 19171215\n', '11635 k 19171222\n', '11700 f 19171231\n', '13878 k 19180806\n', '13890 k 19180810\n', '13905 k 19180812\n', '14828 k 19181126\n', '14861 k 19181127\n', '14930 k 19181202\n', '17632 f 19190728\n', '17695 k 19190802\n', '17763 k 19190814\n', '999999 x 99999999 9\n', 'Sigma_19 7.0 00 14 06 +36 21 08\n', '49294 k 19331030\n', '54515 g 19361030\n', '54554 k 19361110\n', '55722 k 19371015\n', '55723 k 19371015\n', '62664 p 19411112\n', '62832 w 19411126\n', '63918 k 19421020\n', '679

### Initialize astropy table to fill match values

In [19]:
fcolnames = ['Entry Number','Field Name', 'Magnitude', 'RA', 'Dec', 'Equinox','Observations','No. of Observations']
francis_table = Table(names = fcolnames,dtype = [object,object,object,object,object,object,object,object])

need_to_check = []

for i in range(len(match_entries)-1):
    if len(match_entries[i].split()) == 9:
        entry_no = str(int(i))
        dat = match_entries[i].split()
        fname = dat[0]
        mag = dat[1]
        
        rah = dat[2]
        if len(rah) < 2:
            rah = '0' + rah
        ram = dat[3]
        ras = dat[4]
        ra = rah + ' ' + ram + ' ' + ras
        
        dec_d = dat[5]
        decm = dat[6]
        decs = dat[7]
        
        if (len(dat[8].split(',')) <=1) & (len(dec_d.split('.')) > 1):
            declination = dec_d.split('.')
            decd = declination[0]
            mfrac = '.' + declination[1]
            minutes = 60 *float(mfrac)
            mins = str(minutes).split('.')
            decm = mins[0]
            secfrac = '.' + mins[1]
            seconds = 60 *float(secfrac)
            s = str(int(seconds))
            if len(s)<2:
                decs = '0' + s
            else:
                decs = s
            
        else:
            decd = dec_d
        
        dec = decd + ' ' + decm + ' ' + decs
        equinox = dat[8]
        

        val_1 = match_indices[i]
        val_2 = match_indices[i+1] 
        plates = lines[val_1+2:val_2]
        observations = []
        for j in range(len(plates)):
            observations.append(plates[j].replace('\n',''))
        obs = str(observations)
        no_of_obs = val_2 - val_1 - 2
        
        if (len(dat[8].split(',')) >1):
            entry_no = ''
            need_to_check.append(i)
            
        
    else:
        need_to_check.append(i)
        #print(i)
        entry_no = str(int(i))
        fname = ''
        mag = ''
        ra = ''
        dec = ''
        equinox = ''

        
        val_1 = match_indices[i]
        val_2 = match_indices[i+1] 
        plates = lines[val_1+2:val_2]
        observations = []
        for j in range(len(plates)):
            observations.append(plates[j].replace('\n',''))
        obs = str(observations)
        no_of_obs = val_2 - val_1 - 2
        
    francis_table.add_row((entry_no,fname,mag,ra,dec,equinox,obs,no_of_obs))

In [20]:
testing = '+23.5'
decli = testing.split('.')
num = '.'+ decli[1]
minute = 60*float(num)
print(str(minute).split('.'))

['30', '0']


In [21]:
francis_table.show_in_notebook()

In [22]:
#when filling out the table, the entries that were not formatted as the others get flagged 
#and appended to need to check list

print(need_to_check)
#print(francis_table[-2])

[28, 30, 94, 153, 180, 189, 199, 245, 249, 360, 367, 392, 423, 442, 637, 796, 837, 880, 933, 939, 1002, 1024, 1144, 1149, 1200, 1203, 1208, 1216, 1291, 1326, 1367, 1402, 1410, 1446, 1464, 1521, 1623, 1834, 1875, 2031, 2337, 2544, 2567]


In [23]:
### save a copy, edit entries that need to be checked manually, then reimport it
ascii.write(francis_table,'francis_table_tobefixed.csv',format='csv',overwrite=True)


In [24]:
# check entries, look at the entry that needs to be fixed here, fix it in excel, and then write it as a new file
# that will then be reimported as the "fixed" table
#print(match_entries[124])
for i,val in enumerate(need_to_check):
    print (val, match_entries[val])

28 beta_1027 7.5 00 13 21.4 _ _ _

30 Sigma_19 7.0 00 14 06 +36 21 08

94 eta_Cass_A 3.44 00 49 05 +57 48 54 

153 93_Piscium 01 23 33 +18 54 46 1950

180 14092 k 19180903

189 53_Ceti 4.8 01 47 -10 55 59 1950

199 56_And 5.8/11.4<19"_in_78o

245 G174-5 13.9 02 32 50 +52 31.2 1950

249 HR_753 6.0/11.5<164" 02 33 20 +06 00 1950

360 Lal_7443 8.6 03 59 53 35 09 +35 09 17 1950

367 A_Tauri 4.5 04 01 44 +21 49 1950

392 Theta1,2_Tauri 4.0,3.8 04 25 47 +15 51 10

423 4_Orionis 5.2 04 48 32 +05 

442 1305 p 19150226 +10

637 45_Gem 5.6 _ 07 05 30 +16 00 44 1950

796 Ambr_2999 5.2 08 44 42 -01 

837 23_Hydrae 5.4 09 14 13 1950 -06 08 36 1950

880 G118-15 13.8 09 47 00 41 01.2 1950

933 46o1635 9.8 10 28 27 +45 47.5 1950

939 L_825-14 12.7 10 31 15 -11 26.2 1950

1002 Wolf_386 11 21 18 +08 50 _ 1950

1024 L_1405-28 _ 11 39 32 +26 59.6 1950

1144 AC_66o3955 10.5 12 47 03 +66 23.0 1950

1149 Lal_23938 12 45.6 _ -00 13 _ _

1200 G177-31 13.9 13 17 04 45 

1203 G177-34 14.6 13 19 06 +46 39.6 1950


In [ ]:
## still problematic [180, 442]

## Important checkpoint!!
If making any modifications to the TSC.txt file, they should be made to the file below ('francis_table.csv') before reading it in.
<br>
This is the file that has been manually reformatted. If you make changes to TSC.txt, they will not be reflected in further processing. 

In [25]:
## reimport table with fixed entries
francis_table_new = QTable.read('francis_table.csv')

In [26]:
francis_table_new.colnames

['Entry Number',
 'Field Name',
 'Magnitude',
 'RA',
 'Dec',
 'Equinox',
 'Observations',
 'No. of Observations']

In [27]:
fcols = francis_table_new.colnames
for name in fcols:
    francis_table_new[name] = francis_table_new[name].astype(object)


In [28]:
print(len(francis_table_new))
print(len(match_indices))

2576
2577


### Define a function to reformat the RA/Dec values so that they are all unform

In [29]:
def reformat_radec_min(o_ra,o_dec):
    """
    Takes several cases of non-uniform RA/Dec vals and
    and uniformly formats them
    
    Input parameters: index card's original RA, original DEC as a single string
    Returns: RA in format: 00 00 00.00
             Dec in format: 00 00 00.00 
    """
    
    if not ma.is_masked(o_ra):
        rah,ram,ras = o_ra.split()[0],o_ra.split()[1],o_ra.split()[2]


        if len(ram) > 2:
            ra_min = ram[:2]
            ra_sec = "%.2f" % ((float(ram) * 60) % 60)
        else:
            ra_min = ram
            ra_sec = ras


        if ra_min[-1] == '.':
            ra_min = '0' + ra_min[0]

        if (ra_sec != '_'):
            ra_sec = str(ra_sec).zfill(2)

        if (len(ra_sec) < 4) & (ra_sec != '_'):
            ra_sec = ra_sec + '.00'

        
        ra = str(rah).zfill(2) + ' ' + str(ra_min) + ' ' + ra_sec

        
    else:
        ra = ''
        
    if not ma.is_masked(o_dec):
        decd,decm,decs = o_dec.split()[0],o_dec.split()[1],o_dec.split()[2]
        
        
        if len(decm) > 2:
            dec_min = decm[:2]
            dec_sec = "%.2f" % ((float(decm) * 60) % 60)

        else:
            dec_min = decm
            dec_sec = decs
            
        if len(dec_min) < 2:
            dec_min = '0' + dec_min
            
        if (dec_sec != '_'):
            dec_sec = str(dec_sec).zfill(2)
        
        if (len(dec_sec) < 4) & (dec_sec != '_'):
            dec_sec = dec_sec + '.00'
        
        dec = str(decd).zfill(2) + ' ' + str(dec_min) + ' ' + dec_sec

    else:
        dec = ''
        



    return(ra, dec)

In [30]:
print(reformat_radec_min('12 3.3 _','+12 32 _'))

('12 03 18.00', '+12 32 _')


In [31]:
#now run all the RA and Decs from the original table through the function and replace them with the reformatted ones

for i in range(len(francis_table_new)):
    print(i)
    old_ra = francis_table_new[i]['RA']
    old_dec = francis_table_new[i]['Dec']
    ra,dec = reformat_radec_min(old_ra,old_dec)
    francis_table_new[i]['RA'] = ra
    francis_table_new[i]['Dec'] = dec

    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

2123
2124
2125
2126
2127
2128
2129
2130
2131
2132
2133
2134
2135
2136
2137
2138
2139
2140
2141
2142
2143
2144
2145
2146
2147
2148
2149
2150
2151
2152
2153
2154
2155
2156
2157
2158
2159
2160
2161
2162
2163
2164
2165
2166
2167
2168
2169
2170
2171
2172
2173
2174
2175
2176
2177
2178
2179
2180
2181
2182
2183
2184
2185
2186
2187
2188
2189
2190
2191
2192
2193
2194
2195
2196
2197
2198
2199
2200
2201
2202
2203
2204
2205
2206
2207
2208
2209
2210
2211
2212
2213
2214
2215
2216
2217
2218
2219
2220
2221
2222
2223
2224
2225
2226
2227
2228
2229
2230
2231
2232
2233
2234
2235
2236
2237
2238
2239
2240
2241
2242
2243
2244
2245
2246
2247
2248
2249
2250
2251
2252
2253
2254
2255
2256
2257
2258
2259
2260
2261
2262
2263
2264
2265
2266
2267
2268
2269
2270
2271
2272
2273
2274
2275
2276
2277
2278
2279
2280
2281
2282
2283
2284
2285
2286
2287
2288
2289
2290
2291
2292
2293
2294
2295
2296
2297
2298
2299
2300
2301
2302
2303
2304
2305
2306
2307
2308
2309
2310
2311
2312
2313
2314
2315
2316
2317
2318
2319
2320
2321
2322


In [32]:
francis_table_new[235]

<Row index=235 masked=True>
Entry Number Field Name Magnitude     RA         Dec      Equinox                                                                                                                                                                                                                                                                                                     Observations                                                                                                                                                                                                                                                                                                    No. of Observations
   object      object     object    object      object     object                                                                                                                                                                                                                                                                                                        object                                                                                                                                                                                                                                                                                                              object      
------------ ---------- --------- ---------- ------------ ------- ------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------- -------------------
         235   64_Andr.       5.5 02 21 6.00 +49 46 30.00    1950 ['28222 k 19220831 _', '28244 g 19220904 _', '28262 k 19220905 _', '29423 g 19230113 _', '29505 g 19230130 _', '30950 k 19230819 _', '30996 g 19230822 _', '31889 k 19240104 _', '31959 g 19240109 _', '32008 g 19240118 _', '33252 k 19240818 _', '33320 k 19240829 _', '33334 k 19240902 _', '33920 g 19250106 _', '33960 g 19250114 _', '33974 g 19250115 _', '35272 g 19250824 _', '35281 g 19250825 _', '35294 2g 19250826 _', '35982 k 19260123 _', '36880 g 19260828 _', '37410 g 19270117 _', '37418 g 19270124 _', '37421 g 19270127 _', '38296 g 19270825 _', '38338 g 19270901 _', '38350 g 19270902 _']                  27

In [33]:
francis_table_new.show_in_notebook()

### Match between precessed TSC 1950 (or YPC 2000) coordinates and reported coordinates of Index Cards

In [35]:
# convert everything to minutes

def arcminutes(hourangle):
    
    """
    Input parameters: hh mm ss OR dd mm ss
    Returns: minutes of arc or time 
    """
    if not ma.is_masked(hourangle):
        if len(hourangle.split()) >= 3:

            h,m,s = hourangle.split()[0],hourangle.split()[1],hourangle.split()[2] #or degree, 1hr = 60', 1 deg = 60'
            #get rid of +/- in front of dec degrees
            if h[0].isdigit():
                hour = h
            elif h == '_':
                hour = '0'
            else:
                hour = h[1:]
                

            hour = hour.replace('_','0')
            m = m.replace('_','0')
            s = s.replace('_','0')

            hour = float(hour)
            minute = float(m)
            sec = float(s)
            """
            if s != '_':
                sec = float(s)
            else:
                sec = 0            
            """


            minutes = (hour*60) + (minute) + (sec/60)
        else:
            minutes = 0
    else:
        minutes = 0
    return float("%.2f" % minutes)

#print((arcminutes('10 10 30')))
        
        


   

### Search TSC from Francis' Table -- SECTION NO LONGER NEEDED, KEPT FOR RECORDS

In [ ]:
"""def search_match(f_ra,f_dec,equinox='1950',precision=5):
    matches = []
    match_idxs = []
    f_ra_m = arcminutes(f_ra)
    f_dec_m = arcminutes(f_dec)
    for i in range(len(tsc)):
        #print(i)
        t_ra = tsc[i]['RA'+equinox]
        t_dec = tsc[i]['Dec'+equinox]
        if t_ra != '0':
            t_ra_m = arcminutes(t_ra)
            t_dec_m = arcminutes(t_dec)
        else:
            t_ra_m = np.inf
            t_dec_m = np.inf
        if (abs(t_ra_m - f_ra_m) <= precision) & (abs(t_dec_m-f_dec_m)<= precision):
            matches.append(tsc[i]['Thaw Number'])
            match_idxs.append(i)
    return matches,match_idxs
        
       

f_idx = 24
search_ra,search_dec = francis_table_new[f_idx]['RA'],francis_table_new[f_idx]['Dec']
match_thaw, match_thaw_idx = search_match(search_ra,search_dec)
print('Matching Thaw Number:',match_thaw)
print('Matching Thaw Index:', match_thaw_idx)
print(len(match_thaw))"""

In [ ]:
### Search from Francis' Table
#francis_table_new[f_idx]

In [ ]:
### Thaw Result
#tsc[match_thaw_idx]

In [ ]:
#print(len(tsc))
#print(len(francis_table_new))

In [ ]:
"""match_francis = francis_table_new

for i in range(len(match_francis)):
    print(i)
    f_idx = i
    search_ra,search_dec = francis_table_new[f_idx]['RA'],francis_table_new[f_idx]['Dec']
    match_thaw, match_thaw_idx = search_match(search_ra,search_dec)
    if len(match_thaw) >= 1:
        name = tsc[match_thaw_idx]['Thaw Name']
        print(name[0])
        match_francis[i]['TSC No.'] = match_thaw[0]
        match_francis[i]['TSC Name'] = name[0]
    """


In [ ]:
#match_francis.show_in_notebook()

In [ ]:
"""no_of_matches = []
for i in range(len(match_francis)):
    if match_francis[i]['TSC No.']:
        no_of_matches.append(i)
        
print(len(no_of_matches))        
print((len(no_of_matches)/len(match_francis))*100 )"""

### Match TSC by searching Francis' Table


In [36]:
#define a function to search for a match 

def search_match_francis(t_ra,t_dec,search_equinox='1950',precision=5):
    """
    Input parameters: tsc RA, tsc Dec, equinox (default is 1950), precision (default is 5 minutes)
    Returns: matching entry, matching entry index on index card
    
    """
    matches = []
    match_idxs = []
    t_ra_m = arcminutes(t_ra)
    t_dec_m = arcminutes(t_dec)
    for i in range(len(francis_table_new)):
        #print(i)
        f_eq = francis_table_new[i]['Equinox']
        if search_equinox == f_eq:
            f_ra = francis_table_new[i]['RA']
            f_dec = francis_table_new[i]['Dec']
            f_ra_m = arcminutes(f_ra)
            f_dec_m = arcminutes(f_dec)
            if (abs(f_ra_m - t_ra_m) <= precision) & (abs(f_dec_m-t_dec_m)<= precision):
                matches.append(francis_table_new[i]['Entry Number'])
                match_idxs.append(i)
    return matches,match_idxs
        

In [37]:
t_idx = 2589
search_equinox = '1950'
search_ra,search_dec = tsc[t_idx]['Precessed RA'+search_equinox],tsc[t_idx]['Precessed Dec'+search_equinox]
match_f, match_f_idx = search_match_francis(search_ra,search_dec,search_equinox)
print('Matching Francis Number:',match_f)
print('Matching Francis Index:', match_f_idx)
print(len(match_f))

Matching Francis Number: [2534]
Matching Francis Index: [2534]
1


In [38]:
francis_table_new[match_f_idx]


<QTable masked=True length=1>
Entry Number Field Name ... No. of Observations
   object      object   ...        object      
------------ ---------- ... -------------------
        2534  D'Ag_6348 ...                  36

In [39]:
tsc[t_idx]

<Row index=2589 masked=True>
Thaw Number YPC Number YPC Component Thaw Name  YPC Name  BD Number  Thaw RA1900 Thaw Dec1900 Thaw RA1950 Thaw Dec1950 Precessed RA1950 Precessed Dec1950 YPC RA1900 YPC Dec1900   RA2000    Dec2000  Thaw Mag YPC (B-V) YPC V Thaw Spectrum YPC Spectrum Thaw Rel. Parallax Thaw Rel. Parallax Error Delta Pi AO Publication Year Thaw Abs. Parallax Yale Abs. Parallax Yale Abs. Parallax Error Yale Tot. PM Yale PM Position Angle No. of Thaw Observations Thaw Footnotes
    str5      object        str3       str32     str16      str11       str11       str12        str14       str13          str21             str21         str13       str12      str12      str14    str12     str32    str5     str19        str16            str6                  str6            int64          object             int64              str32                 str32              str32             int64                    str3               int64     
----------- ---------- ------------- --------- ---------- ---------- ----------- ------------ ----------- ------------ ---------------- ----------------- ---------- ----------- ---------- --------- -------- --------- ----- ------------- ------------ ------------------ ------------------------ -------- ------------------- ------------------ ------------------ ------------------------ ------------ ---------------------- ------------------------ --------------
       2070    5710.00            -- D'AG 6348 CI 18-3096 +17 4946.0 23 31 00.00 +17 53 00.00          --           --     23 33 29.842    +18 09 37.0692 23 30 58.8   +17 53 02 23 36 06.0 +18 26 34     7.63      7.64   0.7          G5 V       G5   V                 -8                       11       --                1971                 --               20.0                      6.1        0.715                     73                       --             --

## IMPORTANT
### Create a 'Master' table
Add columns to store matched index card information to working TSC
This 'master' table will now include all original thaw published information, all YPC matches, and index card matches

In [40]:
match_tsc = tsc.copy()

###create columns 
match_idx_card = Column(np.zeros(len(tsc)))
field_name = Column(np.zeros(len(tsc)))
mag = Column(np.zeros(len(tsc)))
RA_idx = Column(np.zeros(len(tsc)))
DEC_idx = Column(np.zeros(len(tsc)))
equinox = Column(np.zeros(len(tsc)))
observations = Column(np.zeros(len(tsc)))


###add columns
match_tsc.add_column(match_idx_card, name='Index Card Match Entry')
match_tsc.add_column(field_name,name='Index Card Field Name')
match_tsc.add_column(mag,name='Index Card Mag.')
match_tsc.add_column(RA_idx,name='Index Card RA')
match_tsc.add_column(DEC_idx,name='Index Card Dec')
match_tsc.add_column(equinox,name='Index Card Equinox')
match_tsc.add_column(observations,name='Observations')

###change dtype
match_tsc['Index Card Match Entry'] = match_tsc['Index Card Match Entry'].astype(str)
match_tsc['Index Card Field Name'] = match_tsc['Index Card Field Name'].astype(str)
match_tsc['Index Card Mag.'] = match_tsc['Index Card Mag.'].astype(str)
match_tsc['Index Card RA'] = match_tsc['Index Card RA'].astype(str)
match_tsc['Index Card Dec'] = match_tsc['Index Card Dec'].astype(str)
match_tsc['Index Card Equinox'] = match_tsc['Index Card Equinox'].astype(str)
match_tsc['Observations'] = match_tsc['Observations'].astype(object)


In [41]:
match_tsc.show_in_notebook()

### Search for matches in index card
Two part search. First, go through the whole table and look for 1950 coord matches if that is what is reported on the index card. Then, go through the whole table again and match against 2000 coord matches if that is what is reported instead.

In [42]:
search_equinox='1950'

for i in range(len(match_tsc)):
    print(i)
    t_idx = i
    search_ra,search_dec = tsc[t_idx]['Precessed RA'+search_equinox],tsc[t_idx]['Precessed Dec'+search_equinox]
    match_f, match_f_idx = search_match_francis(search_ra,search_dec,search_equinox)
    if len(match_f) >= 1:
        name = francis_table_new[match_f_idx]['Field Name']
        
        match_tsc[i]['No. of Thaw Observations'] = francis_table_new[match_f_idx]['No. of Observations'][0]
        match_tsc[i]['Index Card Match Entry'] = match_f[0]
        match_tsc[i]['Index Card Field Name'] = name[0]
        match_tsc[i]['Index Card Mag.'] = francis_table_new[match_f_idx]['Magnitude'][0]
        match_tsc[i]['Index Card RA'] = francis_table_new[match_f_idx]['RA'][0]
        match_tsc[i]['Index Card Dec'] = francis_table_new[match_f_idx]['Dec'][0]
        match_tsc[i]['Index Card Equinox'] = francis_table_new[match_f_idx]['Equinox'][0]
        match_tsc[i]['Observations'] = francis_table_new[match_f_idx]['Observations'][0]
    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


In [ ]:
search_equinox='2000'

for i in range(len(match_tsc)):
    print(i)
    t_idx = i
    search_ra,search_dec = tsc[t_idx]['RA'+search_equinox],tsc[t_idx]['Dec'+search_equinox]
    match_f, match_f_idx = search_match_francis(search_ra,search_dec,search_equinox)
    if len(match_f) >= 1:
        name = francis_table_new[match_f_idx]['Field Name']
        
        match_tsc[i]['No. of Thaw Observations'] = francis_table_new[match_f_idx]['No. of Observations'][0]
        match_tsc[i]['Index Card Match Entry'] = match_f[0]
        match_tsc[i]['Index Card Field Name'] = name[0]
        match_tsc[i]['Index Card Mag.'] = francis_table_new[match_f_idx]['Magnitude'][0]
        match_tsc[i]['Index Card RA'] = francis_table_new[match_f_idx]['RA'][0]
        match_tsc[i]['Index Card Dec'] = francis_table_new[match_f_idx]['Dec'][0]
        match_tsc[i]['Index Card Equinox'] = francis_table_new[match_f_idx]['Equinox'][0]
        match_tsc[i]['Observations'] = francis_table_new[match_f_idx]['Observations'][0]

In [ ]:
"""
FOR DR. TURNSHEK!!!!
this line will specify that the YPC no. must be in the format .00, 
run this line for any relevant column to get this format at any stage if 
it gets messed up in reading/writing csv files
"""

match_tsc['YPC Number'].info.format = '.2f'

In [ ]:
match_tsc.show_in_notebook()

In [ ]:
# Check stats of unmatched entries

no_of_matches = []
for i in range(len(match_tsc)):
    if match_tsc[i]['Index Card Match Entry'] == '0.0':
        no_of_matches.append(i)
        
print(len(no_of_matches), 'matches not found')        
print("%.2f" % ((len(no_of_matches)/len(match_tsc))*100), '% of TSC entries did not find an index card match')

In [ ]:
### WRITE THIS AS MASTER TABLE

ascii.write(match_tsc,'master.csv',format='csv',overwrite=True)
#ascii.write(match_tsc, 'master.csv', format='latex' ,overwrite=True) 


### This section is not relevant
### Sort by ascending RA


ra_sort_ids = []
for i in range(len(tsc)):
    ra_sort_ids.append(arcminutes(tsc[i]['Thaw RA1900']))

sort_mask = np.argsort(ra_sort_ids)

In [ ]:
#make a new table for sorted RA
cols = tsc.colnames
ra_sort = Table(names = cols,dtype = [object,object,object,object,object,object,object,object,object,object,object,object,
                                     object,object,object,object,object,object,object,object,object,object,object,object,
                                     object,object,object,object,object])
for i,val in enumerate((sort_mask)):
    ra_sort.add_row(tsc[val])

In [ ]:
ra_sort.show_in_notebook()

In [ ]:
ascii.write(ra_sort,'tsc_sort_thaw1900.csv',fast_writer = False,format='csv',overwrite=True)

## Important
### Create Subtables

In [ ]:
#define colnames and datatype 

match_tsc['Index Card Match Entry'] = match_tsc['Index Card Match Entry'].astype(str)
match_tsc['Index Card Field Name'] = match_tsc['Index Card Field Name'].astype(str)
match_tsc['Index Card Mag.'] = match_tsc['Index Card Mag.'].astype(str)
match_tsc['Index Card RA'] = match_tsc['Index Card RA'].astype(str)
match_tsc['Index Card Dec'] = match_tsc['Index Card Dec'].astype(str)
match_tsc['Index Card Equinox'] = match_tsc['Index Card Equinox'].astype(str)


colnames = ['TPC No', 'AO Publication Year', 'AO Rel. Parallax (err)', 'AO Abs. Parallax (err)','Delta Pi', 'YPC No', 'YPC Abs. Parallax (err)', 
           'AO Name', 'YPC Name', 'BD Name', 'RA2000','Dec2000','AO RA1900','AO Dec1900','YPC Total Proper Motion', 'YPC Proper Motion Position Angle','YPC Spectrum',
           'YPC V Mag', 'YPC B-V Mag','Index Card Match Entry','Index Card Field Name','Index Card Mag.','Index RA','Index Card Dec',
           'Index Card Equinox','AO Obs No, Quality, Date']
vals = [i for i in range(len(colnames))]
for i in range(len(match_tsc)):
    if match_tsc[i]['Thaw RA1900']:
        print(i)
        subtable = Table(names=colnames,masked = True,dtype = [object,object,object,object,object,object,object,object,object,object,
                                                object,object,object,object,object,object,object,object,object,object,object,object,
                                                               object,object,object,object])
        tpc_no = match_tsc[i]['Thaw Number']
        
        ao_pub_date = match_tsc[i]['AO Publication Year'] 
        
        if tsc[i]['Thaw Rel. Parallax']:
            ao_rel_p = match_tsc[i]['Thaw Rel. Parallax'] + str(' (') + match_tsc[i]['Thaw Rel. Parallax Error'] + str(')')
        else:
            ao_rel_p = ""
        
        ao_abs_p = ''
        delta_pi = match_tsc[i]['Delta Pi']
        ypc_no = str(match_tsc[i]['YPC Number'])
        ypc_abs_p = str(match_tsc[i]['Yale Abs. Parallax']) + str(" (") + str(match_tsc[i]['Yale Abs. Parallax Error']) + str(")")
        ao_name = match_tsc[i]['Thaw Name']
        ypc_name = str(match_tsc[i]['YPC Name'])
        bd = match_tsc[i]['BD Number']
        ra2000 = match_tsc[i]['RA2000']
        dec2000 = match_tsc[i]['Dec2000']
        ra1900 = match_tsc[i]['Thaw RA1900']
        dec1900 = match_tsc[i]['Thaw Dec1900']
        pm = str(match_tsc[i]['Yale Tot. PM'])
        pmPA = str(match_tsc[i]['Yale PM Position Angle'])
        
        
        subtable['YPC Spectrum'] = []
        subtable['YPC Spectrum'] = subtable['YPC Spectrum'].astype(object)
        ypc_spec = str(match_tsc['YPC Spectrum'][i])
        
        
  
        subtable['YPC V Mag'] = []
        subtable['YPC V Mag'] = subtable['YPC V Mag'].astype(object)
        ypc_v = str(match_tsc['YPC V'][i])
        
        
        subtable['YPC B-V Mag'] = []
        subtable['YPC B-V Mag'] = subtable['YPC B-V Mag'].astype(object)
        ypc_bv = str(match_tsc['YPC (B-V)'][i])    
        
        """
        Index Card Data Starts Here
        """
        
        ic_entry = match_tsc[i]['Index Card Match Entry']
        ic_fieldname = match_tsc[i]['Index Card Field Name']
        ic_mag = match_tsc[i]['Index Card Mag.']
        ic_ra = match_tsc[i]['Index Card RA']
        ic_dec = match_tsc[i]['Index Card Dec']
        ic_eq = match_tsc[i]['Index Card Equinox']
        
        observations = match_tsc[i]['Observations']
        
        subtable.add_row((tpc_no,ao_pub_date,ao_rel_p,ao_abs_p,delta_pi,ypc_no,ypc_abs_p,ao_name,ypc_name,bd,
                         ra2000,dec2000,ra1900,dec1900,pm,pmPA,ypc_spec,ypc_v,ypc_bv,ic_entry,ic_fieldname,
                          ic_mag,ic_ra,ic_dec,ic_eq,observations))
        
        tpc_no = str(tpc_no)
        cat_no = tpc_no.zfill(4)
        filename = 'AO_'+ str(cat_no) + '_subtable.csv'
        #filename = 'AO_'+ str(cat_no) + '_subtable.tex'  #comment this back in for a tex version
    
        
        ascii.write(subtable, filename, format='csv',fast_writer = False,fill_values=[(ascii.masked, 'N/A')],overwrite=True) 
        #ascii.write(subtable, filename, format='latex' ,overwrite=True)  # uncomment this if you want to save subtables as .tex files
    
    